<a href="https://colab.research.google.com/github/sindhu819/Projects/blob/master/Content_Filtering.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
!apt-get install openjdk-8-jdk-headless -qq > /dev/null
!wget -q https://www-us.apache.org/dist/spark/spark-2.4.4/spark-2.4.4-bin-hadoop2.7.tgz
!tar xf spark-2.4.4-bin-hadoop2.7.tgz
!pip install -q findspark
import findspark
findspark.init("spark-2.4.4-bin-hadoop2.7")# SPARK_HOME
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/content/spark-2.4.4-bin-hadoop2.7"

In [0]:
import numpy as np
import pandas as pd

from operator import add
from pyspark.ml.feature import RegexTokenizer, CountVectorizer
from pyspark.ml.feature import StopWordsRemover, VectorAssembler
from pyspark.ml.feature import Word2Vec, Word2VecModel
from pyspark.ml.feature import IDF

from pyspark.ml import Pipeline, PipelineModel


from pyspark.sql.functions import *

from pyspark.sql.types import *

import folium
import html

In [0]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
import findspark
findspark.init()
from pyspark.sql import SparkSession
spark = SparkSession.builder.master("local[*]").getOrCreate()

In [0]:
users_file=r'/content/drive/My Drive/Project /Data Mining/Dataset/Yelp_Users.csv'
users=spark.read.csv(users_file,header=True)

In [0]:
business_file=r'/content/drive/My Drive/Project /Data Mining/Dataset/Yelp_Business.csv'
business=spark.read.csv(business_file,header=True)


In [0]:
review_file=r'/content/drive/My Drive/Project /Data Mining/Dataset/Yelp_Reviews.parquet'
reviews=spark.read.parquet(review_file)

In [0]:
business.createOrReplaceTempView("business")
users.createOrReplaceTempView("users")
reviews.createOrReplaceTempView("reviews")

In [0]:
business.printSchema()

root
 |-- business_id: string (nullable = true)
 |-- business_name: string (nullable = true)
 |-- address: string (nullable = true)
 |-- city: string (nullable = true)
 |-- state: string (nullable = true)
 |-- postal_code: string (nullable = true)
 |-- latitude: string (nullable = true)
 |-- longitude: string (nullable = true)
 |-- stars: string (nullable = true)
 |-- review_count: string (nullable = true)
 |-- categories: string (nullable = true)



In [0]:
	
spark.sql("SELECT * FROM reviews where business_id='6xgcHeLad-VaoTIQewK84A'").show(3,False)

+----------------------+----------------------+----------------------+-----+-------------------+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+------+-----+----+
|review_id             |user_id               |business_id           |stars|review_date        |review_text                                                                                                                                                          

### Text Processing and Featurization

In [0]:
# create review text dataframe

reviews_text = spark.sql("SELECT business_id, review_text FROM reviews")
reviews_text.show(3,False)

+----------------------+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|business_id           |review_text                                                                                                                                                                                                                                                                                                                                                                                             |
+----------------------+--------------------------------------------------------------------------------------------------------------------------------------------

In [0]:
# concatenate all reviews per restuarant

reviews_text_rdd = reviews_text.rdd
reviews_by_business_rdd = reviews_text_rdd.map(tuple).reduceByKey(add)  
reviews_by_business_df = spark.createDataFrame(reviews_by_business_rdd)
reviews_by_business_df = reviews_by_business_df \
                            .withColumnRenamed('_1', 'business_id') \
                            .withColumnRenamed('_2', 'text')
reviews_by_business_df.count()   

5909

In [0]:
reviews_by_business_df.show(3)

+--------------------+--------------------+
|         business_id|                text|
+--------------------+--------------------+
|eoyvbnRYQe-z85e8R...|We had dinner her...|
|6xgcHeLad-VaoTIQe...|ooooooh yummy.  i...|
|YF4QJ_j-PM7cMZja6...|What an awesome p...|
+--------------------+--------------------+
only showing top 3 rows



In [0]:
# create text processing pipeline -- this a lengthy resouce-intensive process

# Build the pipeline 
regexTokenizer = RegexTokenizer(gaps = False, pattern = '\w+', inputCol = 'text', outputCol = 'token')
stopWordsRemover = StopWordsRemover(inputCol = 'token', outputCol = 'nostopwrd')
countVectorizer = CountVectorizer(inputCol="nostopwrd", outputCol="rawFeature")
iDF = IDF(inputCol="rawFeature", outputCol="idf_vec")
word2Vec = Word2Vec(vectorSize = 100, minCount = 5, inputCol = 'nostopwrd', outputCol = 'word_vec', seed=123)
vectorAssembler = VectorAssembler(inputCols=['idf_vec', 'word_vec'], outputCol='comb_vec')
pipeline = Pipeline(stages=[regexTokenizer, stopWordsRemover, countVectorizer, iDF, word2Vec, vectorAssembler])

In [0]:
# fit the model
pipeline_mdl = pipeline.fit(reviews_by_business_df)

In [0]:
#save the pipeline model
pipeline_mdl.write().overwrite().save('/content/drive/My Drive/Project /Data Mining/pipe_txt')

In [0]:
pipeline_mdl = PipelineModel.load('/content/drive/My Drive/Project /Data Mining/pipe_txt')

In [0]:

# transform the review data

reviews_by_business_trf_df = pipeline_mdl.transform(reviews_by_business_df)

In [0]:

reviews_by_business_trf_df.select( 'text', 'nostopwrd', 'idf_vec', 'word_vec', 'comb_vec').show(10)

+--------------------+--------------------+--------------------+--------------------+--------------------+
|                text|           nostopwrd|             idf_vec|            word_vec|            comb_vec|
+--------------------+--------------------+--------------------+--------------------+--------------------+
|We had dinner her...|[dinner, food, ex...|(260453,[0,1,2,3,...|[-0.0138955641563...|(260553,[0,1,2,3,...|
|ooooooh yummy.  i...|[ooooooh, yummy, ...|(260453,[0,1,2,3,...|[0.00304312064714...|(260553,[0,1,2,3,...|
|What an awesome p...|[awesome, pool, p...|(260453,[0,1,2,3,...|[-0.0609865790550...|(260553,[0,1,2,3,...|
|Go. Seriously. Yo...|[go, seriously, d...|(260453,[0,1,2,3,...|[-0.0051622267374...|(260553,[0,1,2,3,...|
|Amazing service, ...|[amazing, service...|(260453,[0,1,2,3,...|[-0.0065394036136...|(260553,[0,1,2,3,...|
|I went here yeste...|[went, yesterday,...|(260453,[0,1,2,3,...|[-0.0592415392973...|(260553,[0,1,2,3,...|
|The Four Stars = ...|[four, stars, e

In [0]:
reviews_by_business_trf_df.printSchema()

root
 |-- business_id: string (nullable = true)
 |-- text: string (nullable = true)
 |-- token: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- nostopwrd: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- rawFeature: vector (nullable = true)
 |-- idf_vec: vector (nullable = true)
 |-- word_vec: vector (nullable = true)
 |-- comb_vec: vector (nullable = true)



In [0]:
reviews_by_business_trf_df.count()

5909

In [0]:
reviews_by_business_trf_df.take(3)

[Row(business_id='eoyvbnRYQe-z85e8Rc6vAg', text='We had dinner here and the food was excellent and the service couldn\'t have been better! Thanks Jose!  We will be back for sure.Jason recommended the penne shrimp dish its was awesome. Definitely request Jason as your waiter. We will be backThe meatballs and chicken dishes are great but the service is a boo boo.  The waiter forgot one of our meals plus we had to search for him.  If they improve their service, we will certainly come back.I would give this place 4 stars but for the price, I expected the food to be above average.  I had the Penne Chicken Pasta and there was nothing special about it.  If this restaurant wasn\'t in a Casio, they would charge half the price.  I\'m not saying it was bad, just not anything special.  Service was very good though.They suckered me by just smelling the pizza as I walked by! But what really got me was their wine special...was really wanting a very good glass of wine on this last night of our adventu

In [0]:
def CosineSim(vec1, vec2): 
    return np.dot(vec1, vec2) / np.sqrt(np.dot(vec1, vec1)) / np.sqrt(np.dot(vec2, vec2))

In [0]:

all_business_vecs = reviews_by_business_trf_df.select('business_id', 'word_vec').rdd.map(lambda x: (x[0], x[1])).collect()

In [0]:
reviews_by_business_trf_df.select('business_id', 'word_vec').repartition(3).write.json("/content/drive/My Drive/Project /Data Mining/Dataset/Result/content.csv")

In [0]:
len(all_business_vecs)

5909

In [0]:
# peek at one row

all_business_vecs[0]

('eoyvbnRYQe-z85e8Rc6vAg',
 DenseVector([-0.0139, 0.007, 0.1019, 0.0236, 0.0184, -0.0273, -0.0346, 0.0284, -0.0389, -0.0294, 0.0517, -0.0099, 0.007, -0.0258, 0.0253, 0.0513, 0.0135, -0.0068, 0.0227, -0.0177, -0.0042, -0.0066, 0.001, 0.0171, -0.0581, -0.1022, 0.0232, -0.0208, -0.0089, 0.014, 0.0095, -0.0108, 0.0081, 0.0135, -0.0294, 0.0541, 0.0192, 0.0053, -0.065, 0.0562, 0.0503, 0.0224, -0.0112, 0.004, -0.038, 0.0708, -0.0061, 0.0185, 0.0457, 0.0343, -0.0181, -0.0665, 0.0192, 0.0784, -0.0455, -0.0233, 0.081, 0.0331, 0.0005, -0.0251, 0.0278, -0.0172, -0.0044, 0.0252, 0.0687, 0.0238, 0.0604, 0.03, -0.024, 0.0098, 0.0144, -0.0007, -0.0387, -0.0036, 0.0014, -0.0112, 0.0552, -0.0084, -0.0168, 0.0722, -0.0411, -0.0013, 0.0557, -0.0278, 0.0101, 0.0415, 0.0782, 0.0375, -0.0463, 0.0426, 0.0741, 0.0214, 0.0137, 0.0315, 0.0123, -0.0078, 0.004, -0.0149, 0.0534, 0.0108]))

In [0]:
# the first item is the business id

all_business_vecs[1][0]

'6xgcHeLad-VaoTIQewK84A'

In [0]:

# the second item is the vector represntation (word2vec) of all review text of that restaurant

all_business_vecs[1][1]

DenseVector([0.003, -0.0149, 0.1091, 0.0113, 0.0308, -0.0443, -0.0315, 0.0155, -0.0461, -0.0062, 0.0344, 0.0033, -0.0066, -0.0565, -0.0109, 0.0311, 0.0072, -0.0123, -0.0037, -0.024, -0.0232, -0.0127, 0.0102, 0.0413, -0.0638, -0.1054, 0.0091, -0.0489, -0.0018, 0.0216, 0.0147, -0.0146, 0.0088, 0.0362, -0.0162, 0.0477, 0.0445, 0.0195, -0.0542, 0.0661, 0.0608, 0.004, 0.0016, -0.0136, 0.0229, 0.0819, -0.0053, 0.0391, 0.0514, 0.0314, -0.0419, -0.0646, -0.0031, 0.0432, -0.0504, -0.045, 0.0522, 0.0346, 0.0203, -0.0361, 0.0242, -0.0197, -0.003, 0.0118, 0.0545, 0.0421, 0.0758, 0.0542, -0.0022, 0.0146, 0.0152, -0.0137, -0.0626, 0.0185, -0.0079, -0.036, 0.0569, -0.0143, -0.0217, 0.0539, -0.0141, -0.0191, 0.0721, -0.0354, 0.0112, 0.0343, 0.0829, 0.0094, -0.0573, 0.0176, 0.0679, 0.0457, 0.0211, 0.0541, 0.0007, -0.0159, -0.0132, -0.028, 0.0329, 0.019])

In [0]:
def getSimilarBusinesses(b_ids, sim_bus_limit=10):
    
    schema = StructType([   
                            StructField("business_id", StringType(), True)
                            ,StructField("score", IntegerType(), True)
                            ,StructField("input_business_id", StringType(), True)
                        ])
    
    similar_businesses_df = spark.createDataFrame([], schema)
    
    for b_id in b_ids:
        
        input_vec = [(r[1]) for r in all_business_vecs if r[0] == b_id][0]
        #input_vec = reviews_by_business_trf_df.select('word_vec')\
                    #.filter(reviews_by_business_trf_df['business_id'] == b_id)\
                    #.collect()[0][0]

        similar_business_rdd = spark.sparkContext.parallelize((i[0], float(CosineSim(input_vec, i[1]))) for i in all_business_vecs)

        similar_business_df = spark.createDataFrame(similar_business_rdd) \
            .withColumnRenamed('_1', 'business_id') \
            .withColumnRenamed('_2', 'score') \
            .orderBy("score", ascending = False)
            
        similar_business_df = similar_business_df.filter(col("business_id") != b_id).limit(sim_bus_limit)
        similar_business_df = similar_business_df.withColumn('input_business_id', lit(b_id))
        
        similar_businesses_df = similar_businesses_df \
                                    .union(similar_business_df)
        
    
    return similar_businesses_df

In [0]:
def getBusinessDetails(in_bus):
    
    a = in_bus.alias("a")
    b = business.alias("b")
    
    return a.join(b, col("a.business_id") == col("b.business_id"), 'inner') \
             .select([col('a.'+xx) for xx in a.columns] + [col('b.business_name'),col('b.categories'),
                                                           col('b.stars'),col('b.review_count'),
                                                           col('b.latitude'),col('b.longitude')])

In [0]:
def showInMap(df):
    mp = folium.Map(location=[36.1699, -115.1398], zoom_start=12)
    for i, r in df.toPandas().iterrows():
      print(r)
      folium.Marker(location =[float(r.latitude), float(r.longitude)], popup = html.escape(r["business_name"]) + '<br>' + 'Stars: ' + str(r.stars) + '<br>' + 'Reviews: ' + str(r.review_count),    icon = folium.Icon(color='green')).add_to(mp)
    return mp

In [0]:

# test with one restaurant

bids = ['6xgcHeLad-VaoTIQewK84A']

print('\ninput restaurants details:')
business.select('business_id','business_name', 'categories') \
    .filter(business.business_id.isin(bids) == True).show(truncate=False)
    
# get top 10 similar business
sims = getBusinessDetails(getSimilarBusinesses(bids))

print('Top 10 similar restaurants for each input restaurant are:"')
sims.select('input_business_id','business_name', 'score','categories').toPandas()


input restaurants details:
+----------------------+---------------+---------------------------------------------------------+
|business_id           |business_name  |categories                                               |
+----------------------+---------------+---------------------------------------------------------+
|6xgcHeLad-VaoTIQewK84A|N9NE Steakhouse|Seafood, Steakhouses, American (Traditional), Restaurants|
+----------------------+---------------+---------------------------------------------------------+

Top 10 similar restaurants for each input restaurant are:"


input_business_id  ...                                         categories
0  6xgcHeLad-VaoTIQewK84A  ...  Restaurants, Seafood, Desserts, Steakhouses, Food
1  6xgcHeLad-VaoTIQewK84A  ...  Nightlife, Bars, Steakhouses, American (Tradit...
2  6xgcHeLad-VaoTIQewK84A  ...                           Steakhouses, Restaurants
3  6xgcHeLad-VaoTIQewK84A  ...                           Restaurants, Steakhouses
4  6xgcHeLad-VaoTIQewK84A  ...                           Steakhouses, Restaurants
5  6xgcHeLad-VaoTIQewK84A  ...  Nightlife, Restaurants, Bars, Steakhouses, Ame...
6  6xgcHeLad-VaoTIQewK84A  ...                  Restaurants, Steakhouses, Seafood
7  6xgcHeLad-VaoTIQewK84A  ...       Breakfast & Brunch, Steakhouses, Restaurants
8  6xgcHeLad-VaoTIQewK84A  ...  Restaurants, Steakhouses, Seafood, American (N...
9  6xgcHeLad-VaoTIQewK84A  ...                           Restaurants, Steakhouses

[10 rows x 4 columns]

In [0]:
def getContentRecoms(u_id, sim_bus_limit=10):
    
    # select restaurants previously reviewed (3+) by the user
    query = """
    SELECT distinct(business_id),user_id FROM reviews  
    where stars >= 3.0 
    and user_id = "{}"
    """.format(u_id)

    usr_rev_bus = spark.sql(query)
    
    # from these get sample of 5 restaurants
    usr_rev_bus = usr_rev_bus.limit(5)

    usr_rev_bus_det = getBusinessDetails(usr_rev_bus)
    
    # show the sample details
    print('\nBusinesses previously reviewed by user:')
    usr_rev_bus_det.select(['business_id', 'business_name', 'categories']).show(truncate = False)

    bus_list = [i.business_id for i in usr_rev_bus.collect()]

    # get restaurants similar to the sample
    sim_bus_df = getSimilarBusinesses(bus_list, sim_bus_limit)

    # filter out those have been reviewd before by the user
    s = sim_bus_df.alias("s")
    r = usr_rev_bus.alias("r")
    j = s.join(r, col("s.business_id") == col("r.business_id"), 'left_outer') \
         .where(col("r.business_id").isNull()) \
         .select([col('s.business_id'),col('s.score'),col('r.user_id')])

    a = j.orderBy("score", ascending = False).limit(sim_bus_limit)
    dft = getBusinessDetails(a)
    dft.show(truncate=False)
    return getBusinessDetails(a),usr_rev_bus_det

In [0]:
result_df = getContentRecoms('3nDUQBjKyVor5wV0reJChg')


Businesses previously reviewed by user:
+----------------------+-----------------------+--------------------------------------------------------------------------------+
|business_id           |business_name          |categories                                                                      |
+----------------------+-----------------------+--------------------------------------------------------------------------------+
|oGYXSVs0ympLy0ur8Qnp7g|Taqueria El Buen Pastor|Mexican, Restaurants                                                            |
|E67gGK8yOn9kkNzx8FzQKA|Buffalo Wild Wings     |Bars, Sports Bars, Nightlife, Chicken Wings, American (Traditional), Restaurants|
|UcIrRf2mWgqqlg-HNoDl0A|China One              |Chinese, Restaurants                                                            |
|SeNOJ2zYHziptxLuiRINLg|Lago                   |Italian, Restaurants, Tapas/Small Plates                                        |
|tv4nFQ-1a8Lm9B-tIpBjyg|Shin Yakitori House    |J

In [0]:
result_df.printSchema()

root
 |-- business_id: string (nullable = true)
 |-- score: double (nullable = true)
 |-- user_id: string (nullable = true)
 |-- business_name: string (nullable = true)
 |-- categories: string (nullable = true)
 |-- stars: string (nullable = true)
 |-- review_count: string (nullable = true)
 |-- latitude: string (nullable = true)
 |-- longitude: string (nullable = true)



In [0]:
result_df.show(3,False)

+-----------+-----+-------+-------------+----------+-----+------------+--------+---------+
|business_id|score|user_id|business_name|categories|stars|review_count|latitude|longitude|
+-----------+-----+-------+-------------+----------+-----+------------+--------+---------+
+-----------+-----+-------+-------------+----------+-----+------------+--------+---------+



In [0]:
p_df = result_df.toPandas()

In [0]:
p_df['user_id']

In [0]:
showInMap(content_recom_df)

business_id                                 16Fplxu-OwVmTEFxQAUP4g
score                                                     0.984222
business_name                                    TENDER Steakhouse
categories       Nightlife, Restaurants, Bars, Steakhouses, Ame...
stars                                                          3.5
review_count                                                   473
latitude                                             36.0953556397
longitude                                           -115.176614273
Name: 0, dtype: object
business_id                                 bjSC_jbrypke0l-bXXBmwQ
score                                                     0.983289
business_name                           Vic & Anthony's Steakhouse
categories       Restaurants, Steakhouses, Seafood, American (N...
stars                                                          4.5
review_count                                                   692
latitude                               

In [0]:
def getKeyWordsRecoms(key_words, sim_bus_limit):
    
    print('\nBusinesses similar to key words: "' + key_words + '"')
    
    input_words_df = spark.sparkContext.parallelize([(0, key_words)]).toDF(['business_id', 'text'])
    
    # transform the the key words to vectors
    input_words_df = pipeline_mdl.transform(input_words_df)
    
    # choose word2vec vectors
    input_key_words_vec = input_words_df.select('word_vec').collect()[0][0]
    
    # get similarity
    sim_bus_byword_rdd = spark.sparkContext.parallelize((i[0], float(CosineSim(input_key_words_vec, i[1]))) for i in all_business_vecs)

    sim_bus_byword_df = spark.createDataFrame(sim_bus_byword_rdd) \
         .withColumnRenamed('_1', 'business_id') \
         .withColumnRenamed('_2', 'score') \
         .orderBy("score", ascending = False)
    
    # return top 10 similar businesses
    a = sim_bus_byword_df.limit(sim_bus_limit)
    return getBusinessDetails(a)

In [0]:
# test key word similarity to review text

key_words = 'chicken cheese burger'

keywords_recom_df = getKeyWordsRecoms(key_words, 10)
keywords_recom_df.toPandas()


Businesses similar to key words: "chicken cheese burger"


business_id     score  ...       latitude        longitude
0  cxnbk6t6L3jnfT5n2Hbl3Q  0.529038  ...     36.2714625     -115.2676299
1  U-Uj13i0RkwgZ8e7I4Lf8w  0.523883  ...  36.1050061565  -115.1752979109
2  g7fXSjIsE31hLIW5z60zfg  0.587655  ...      36.128561     -115.1711298
3  0UESjBq6_kPjCs4zPh4oEQ  0.567740  ...  36.1219516351  -115.1664865184
4  zblKqBFWq7HMACwacMpzig  0.526208  ...      36.069088      -115.119841
5  5exz18duMXvg91ZPdNX3eA  0.514153  ...     36.1143022     -115.1721025
6  LklWSvyLZXN3tEGxT8rIfg  0.523576  ...     36.1090156      -115.172312
7  0SNSRmPbydrspRqWz82F5Q  0.674533  ...     35.9208835     -115.1652008
8  JTknlKD6bviJZLngdpbydw  0.551822  ...     36.1725319      -115.197258
9  tZW4NLpEYinu4mIxdKj0Pw  0.518299  ...     36.1585755     -115.0996395

[10 rows x 8 columns]

In [0]:
showInMap(keywords_recom_df)

business_id      cxnbk6t6L3jnfT5n2Hbl3Q
score                          0.529038
business_name           SinCity Burgers
categories         Burgers, Restaurants
stars                               3.0
review_count                         72
latitude                     36.2714625
longitude                  -115.2676299
Name: 0, dtype: object
business_id                                 U-Uj13i0RkwgZ8e7I4Lf8w
score                                                     0.523883
business_name                              Original Chicken Tender
categories       Food Court, Fast Food, Restaurants, Hot Dogs, ...
stars                                                          3.5
review_count                                                    31
latitude                                             36.1050061565
longitude                                          -115.1752979109
Name: 1, dtype: object
business_id                                 g7fXSjIsE31hLIW5z60zfg
score                          